In [1]:
import gymnasium as gym
from pogema import GridConfig
from stable_baselines3 import DQN, A2C
from stable_baselines3.common.evaluation import evaluate_policy

%load_ext autoreload
%autoreload 2
%matplotlib inline

grid_config = GridConfig(
    size=8,
    density=0.3,
    num_agents=1,
    max_episode_steps=30
)

env = gym.make("Pogema-v0",grid_config=grid_config)

a2c_model = A2C(
    "MlpPolicy",
    env,
    verbose=1
)

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/gymnasium/utils/passive_env_checker.py:29: UserWarning: WARN: It seems a Box observation space is an image but the `dtype` is not `np.uint8`, actual type: float32. If the Box observation space is not an image, we recommend flattening the observation to have only a 1D vector.
  logger.warn(
/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/gymnasium/utils/passive_env_checker.py:34: UserWarning: WARN: It seems a Box observation space is an image but the lower and upper bounds are not [0, 255]. Actual lower bound: -1.0, upper bound: 1.0. Generally, CNN policies assume observations are within that range, so you may encounter an issue if the observation values are not.
  logger.warn(


#### Optuna Integration

In [2]:
""" Optuna example that optimizes the hyperparameters of
a reinforcement learning agent using A2C implementation from Stable-Baselines3
on a Gymnasium environment.

This is a simplified version of what can be found in https://github.com/DLR-RM/rl-baselines3-zoo.

You can run this example as follows:
    $ python sb3_simple.py

"""
from typing import Any
from typing import Dict

import gymnasium
import optuna
from optuna.pruners import MedianPruner
from optuna.samplers import TPESampler
from stable_baselines3 import A2C
from stable_baselines3.common.callbacks import EvalCallback
from stable_baselines3.common.monitor import Monitor
import torch
import torch.nn as nn


N_TRIALS = 100
N_STARTUP_TRIALS = 5
N_EVALUATIONS = 2
N_TIMESTEPS = int(1.2e5)
EVAL_FREQ = int(N_TIMESTEPS / N_EVALUATIONS)
N_EVAL_EPISODES = 3


DEFAULT_HYPERPARAMS = {
    "policy": "MlpPolicy",
    "verbose": 1,
    "env": env
}

def sample_a2c_params(trial: optuna.Trial) -> Dict[str, Any]:
    """Sampler for A2C hyperparameters."""
    gamma = 1.0 - trial.suggest_float("gamma", 0.0001, 0.1, log=True)
    learning_rate = trial.suggest_float("lr", 1e-5, 1, log=True)

    trial.set_user_attr("gamma", gamma)

    return {
        "gamma": gamma,
        "learning_rate": learning_rate,
    }


class TrialEvalCallback(EvalCallback):
    """Callback used for evaluating and reporting a trial."""

    def __init__(
        self,
        eval_env: gymnasium.Env,
        trial: optuna.Trial,
        n_eval_episodes: int = 5,
        eval_freq: int = 10000,
        deterministic: bool = True,
        verbose: int = 0,
    ):
        super().__init__(
            eval_env=eval_env,
            n_eval_episodes=n_eval_episodes,
            eval_freq=eval_freq,
            deterministic=deterministic,
            verbose=verbose,
        )
        self.trial = trial
        self.eval_idx = 0
        self.is_pruned = False

    def _on_step(self) -> bool:
        if self.eval_freq > 0 and self.n_calls % self.eval_freq == 0:
            super()._on_step()
            self.eval_idx += 1
            self.trial.report(self.last_mean_reward, self.eval_idx)
            # Prune trial if need.
            if self.trial.should_prune():
                self.is_pruned = True
                return False
        return True


def objective(trial: optuna.Trial) -> float:
    kwargs = DEFAULT_HYPERPARAMS.copy()
    # Sample hyperparameters.
    kwargs.update(sample_a2c_params(trial))
    # Create the RL model.
    model = A2C(**kwargs)
    # Create env used for evaluation.
    eval_env = Monitor(env)
    # Create the callback that will periodically evaluate and report the performance.
    eval_callback = TrialEvalCallback(
        eval_env, trial, n_eval_episodes=N_EVAL_EPISODES, eval_freq=EVAL_FREQ, deterministic=True
    )

    nan_encountered = False
    try:
        model.learn(N_TIMESTEPS, callback=eval_callback)
    except AssertionError as e:
        # Sometimes, random hyperparams can generate NaN.
        print(e)
        nan_encountered = True
    finally:
        # Free memory.
        model.env.close()
        eval_env.close()

    # Tell the optimizer that the trial failed.
    if nan_encountered:
        return float("nan")

    if eval_callback.is_pruned:
        raise optuna.exceptions.TrialPruned()

    return eval_callback.last_mean_reward


if __name__ == "__main__":
    # Set pytorch num threads to 1 for faster training.
    torch.set_num_threads(1)

    sampler = TPESampler(n_startup_trials=N_STARTUP_TRIALS)
    # Do not prune before 1/3 of the max budget is used.
    pruner = MedianPruner(n_startup_trials=N_STARTUP_TRIALS, n_warmup_steps=N_EVALUATIONS // 3)

    study = optuna.create_study(sampler=sampler, pruner=pruner, direction="maximize")
    try:
        study.optimize(objective, n_trials=N_TRIALS, n_jobs=4)
    except KeyboardInterrupt:
        pass

    print("Number of finished trials: ", len(study.trials))

    print("Best trial:")
    trial = study.best_trial

    print("  Value: ", trial.value)

    print("  Params: ")
    for key, value in trial.params.items():
        print("    {}: {}".format(key, value))

    print("  User attrs:")
    for key, value in trial.user_attrs.items():
        print("    {}: {}".format(key, value))


/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
[W ParallelNative.cpp:230] Warning: Cannot set number of intraop threads after parallel work has started or after set_num_threads call when using native parallel backend (function set_num_threads)
[I 2023-11-05 19:17:20,572] A new study created in memory with name: no-name-2271a94c-47cf-49b3-b3a1-8acbb5ae4497


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 20.6     |
|    ep_rew_mean        | 0.364    |
| time/                 |          |
|    fps                | 235      |
|    iterations         | 100      |
|    time_elapsed       | 2        |
|    total_timesteps    | 500      |
| train/                |          |
|    entropy_loss       | -1.61    |
|    explained_variance | -21.5    |
|    learning_rate      | 3.41e-05 |
|    n_updates          | 99       |
|    policy_loss        | 0.12     |
|    value_loss         | 0.0126   |
--------------------------------

[I 2023-11-05 19:24:59,257] Trial 2 finished with value: 0.0 and parameters: {'gamma': 0.0010533686291300326, 'lr': 0.28153746448902656}. Best is trial 2 with value: 0.0.


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
------------------------------------
| eval/                 |          |
|    mean_ep_length     | 49.3     |
|    mean_reward        | 0.333    |
| time/                 |          |
|    total_timesteps    | 120000   |
| train/                |          |
|    entropy_loss       | -1.59    |
|    explained_variance | -5.25    |
|    learning_rate      | 4.93e-05 |
|    n_updates          | 23999    |
|    policy_loss        | 0.00932  |
|    value_loss         | 0.000497 |
------------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 25.9     |
|    ep_rew_mean     | 0.33     |
| time/              |          |
|    fps             | 261      |
|    iterations      | 24000    |
|    time_elapsed    | 458      |
|    total_timesteps | 120000   |
---------------------------------


[I 2023-11-05 19:24:59,366] Trial 0 finished with value: 0.3333333333333333 and parameters: {'gamma': 0.00011138443927042074, 'lr': 4.930438883401521e-05}. Best is trial 0 with value: 0.3333333333333333.


...

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 24.6      |
|    ep_rew_mean        | 0.2       |
| time/                 |           |
|    fps                | 254       |
|    iterations         | 23600     |
|    time_elapsed       | 463       |
|    total_timesteps    | 118000    |
| train/                |           |
|    entropy_loss       | -4.86e-05 |
|    explained_variance | -52.5     |
|    learning_rate      | 0.00314   |
|    n_updates          | 23599     |
|    policy_loss        | -2.63e-08 |
|    value_loss         | 5.98e-05  |
-------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 27.1     |
|    ep_rew_mean        | 0.11     |
| time/                 |          |
|    fps                | 255      |
|    iterations         | 23800    |
|

[I 2023-11-05 20:28:08,441] Trial 30 finished with value: 0.3333333333333333 and parameters: {'gamma': 0.0006729174889033615, 'lr': 0.004536288569949908}. Best is trial 27 with value: 1.0.


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 24.4      |
|    ep_rew_mean        | 0.12      |
| time/                 |           |
|    fps                | 277       |
|    iterations         | 7100      |
|    time_elapsed       | 127       |
|    total_timesteps    | 35500     |
| train/                |           |
|    entropy_loss       | -0.00045  |
|    explained_variance | -2.55e+03 |
|    learning_rate      | 0.00479   |
|    n_updates          | 7099      |
|    policy_loss        | 1.26e-08  |
|    value_loss         | 1.51e-06  |
-------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 22.9      |
|    ep_rew_mean        | 0.18      |
| time/                 |           |
|    fps                | 254       |
|    iterations         | 23900 

[I 2023-11-05 20:28:11,967] Trial 31 finished with value: 0.0 and parameters: {'gamma': 0.0007514922696902498, 'lr': 0.003135578477716134}. Best is trial 27 with value: 1.0.


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 36.3     |
|    ep_rew_mean        | 0.0741   |
| time/                 |          |
|    fps                | 267      |
|    iterations         | 200      |
|    time_elapsed       | 3        |
|    total_timesteps    | 1000     |
| train/                |          |
|    entropy_loss       | -0.0107  |
|    explained_variance | -44.2    |
|    learning_rate      | 0.004    |
|    n_updates          | 199      |
|    policy_loss        | 2.47e-06 |
|    value_loss         | 7.12e-06 |
------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 25.4      |
|    ep_rew_mean        | 0.13      |
| time/                 |           |
|    fps                | 277       |
|    iterations         | 7300      |
|    time_e

### Train agent with best hyper parameters

In [23]:
a2c_model = A2C(
    "MlpPolicy",
    env,
    verbose=1,
    gamma=1-0.001583962761136084,
    learning_rate=0.00030466139396632876,
)

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


In [24]:
# Train agent and save it
a2c_model.learn(int(1.2e5))
a2c_model.save("saved/a2c_baseline")

-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 28.3      |
|    ep_rew_mean        | 0.176     |
| time/                 |           |
|    fps                | 2091      |
|    iterations         | 100       |
|    time_elapsed       | 0         |
|    total_timesteps    | 500       |
| train/                |           |
|    entropy_loss       | -1.61     |
|    explained_variance | -1.25e+03 |
|    learning_rate      | 0.000305  |
|    n_updates          | 99        |
|    policy_loss        | 0.0797    |
|    value_loss         | 0.0024    |
-------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 26.1      |
|    ep_rew_mean        | 0.263     |
| time/                 |           |
|    fps                | 2117      |
|    iterations         | 200       |
|    time_elapsed       | 0         |
|    total_timesteps    | 1000      |
| train/    

#### Testing 

In [25]:
a2c_model = A2C.load("saved/a2c_baseline")

env.reset()

mean_reward, std_reward = evaluate_policy(a2c_model, env, deterministic=True, n_eval_episodes=20)
print(f"mean_reward:{mean_reward:.2f} +/- {std_reward:.2f}")

mean_reward:0.15 +/- 0.36


/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


In [26]:
# RANDOM SEED
from IPython.display import SVG, display
from pogema.animation import AnimationMonitor, AnimationConfig

env = AnimationMonitor(env)

def evaluate_success_rate(model, env, num_episodes=100):
    success_count = 0
    step_array = []
    for i in range(num_episodes):
        print(f'---{i}---')
        obs = env.reset()

        # Check if observation is a tuple and extract the first element if true.
        if isinstance(obs, tuple):
            obs = obs[0]
        max_step = 100
        steps_taken = 0
        done = truncated = False
        while not done and max_step > 0:
            action, _ = model.predict(obs)
            next_obs, reward, done, truncated, info = env.step(action)
            print(action,max_step,success_count,done)
            max_step -= 1
            steps_taken += 1
            # Check if next_obs is a tuple and extract the first element if true.
            if isinstance(next_obs, tuple):
                next_obs = next_obs[0]
            obs = next_obs

            # Check if agent was successful in that episode.
            if done:
                success_count += 1
                step_array.append(steps_taken)
                env.save_animation(f"render{i}.svg", AnimationConfig(egocentric_idx=0))
                break

    success_rate = success_count / num_episodes
    return success_rate, step_array

success_rate,step_array = evaluate_success_rate(a2c_model, env)
print(f"Agent Success Rate: {success_rate * 100:.2f}%")
print(f"steps to termination : {step_array}")

---0---
2 100 0 False
2 99 0 False
3 98 0 False
4 97 0 False
1 96 0 False
2 95 0 False
3 94 0 False
4 93 0 False
3 92 0 False
4 91 0 False
3 90 0 False
4 89 0 False
0 88 0 False
1 87 0 False
2 86 0 False
3 85 0 False
0 84 0 False
3 83 0 False
2 82 0 False
2 81 0 False
4 80 0 False
0 79 0 False
3 78 0 False
4 77 0 False
3 76 0 False
2 75 0 False
3 74 0 False
2 73 0 False
2 72 0 False
2 71 0 False
2 70 0 False
2 69 0 False
2 68 0 False
2 67 0 False
2 66 0 False
2 65 0 False
2 64 0 False
2 63 0 False
2 62 0 False
2 61 0 False
2 60 0 False
2 59 0 False
2 58 0 False
2 57 0 False
2 56 0 False
2 55 0 False
2 54 0 False
2 53 0 False
2 52 0 False
2 51 0 False
2 50 0 False
2 49 0 False
2 48 0 False
2 47 0 False
2 46 0 False
2 45 0 False
2 44 0 False
2 43 0 False
2 42 0 False
2 41 0 False
2 40 0 False
2 39 0 False
2 38 0 False
2 37 0 False
2 36 0 False
2 35 0 False
2 34 0 False
2 33 0 False
2 32 0 False
2 31 0 False
2 30 0 False
2 29 0 False
2 28 0 False
2 27 0 False
2 26 0 False
2 25 0 False
2 2

In [ ]:
# we got 35% success rate for 1.25e5 steps
# we got 7% success rate for 3.0e5 steps
# better to use 1.25e5 steps